In [72]:
!pip install -q transformers pytorch-lightning
!pip install pandas
! pip install transformers datasets evaluate
! pip install timm
! pip install -U accelerate

#(1) hugging face에 write token으로 로그인
#로그인을 해야 train 가능
from huggingface_hub import notebook_login

notebook_login()

import pandas as pd
from datasets import load_dataset
import numpy as np
import os
from PIL import Image, ImageDraw
import random
from transformers import AutoImageProcessor, AutoModelForObjectDetection, TrainingArguments, Trainer, pipeline
import albumentations
import numpy as np
import torch
import json
import torchvision
import evaluate
from tqdm import tqdm
import requests

use_data = load_dataset("Multimodal-Fatima/OK-VQA_train")

# 처음 200개의 데이터를 가져옵니다.
used_data = use_data['train'][:200]

# 데이터셋의 구조 확인
print(f"Type of used_data: {type(used_data)}")

# 선택할 특성
selected_features_to_keep = ['question', 'answers', 'image']

# 새로운 데이터를 담을 리스트 초기화
new_data = []

# 기존 데이터에서 선택한 특성만 포함한 새로운 데이터 생성
new_data_point = {feature: used_data.get(feature) for feature in selected_features_to_keep}
new_data.append(new_data_point)

# 결과 출력
for data_point in new_data:
    print("New Data Point:")
    for feature in selected_features_to_keep:
        print(f"{feature}: {data_point.get(feature)}")
    print()
# 'answers'의 첫 번째 답변만 선택
selected_answers = [ans[0] for ans in used_data['answers']]

# LabelEncoder를 사용하여 답변을 id로 매핑
label_encoder = LabelEncoder()
encoded_labels = label_encoder.fit_transform(selected_answers)

# 매핑된 id를 데이터셋에 추가
used_data['label_ids'] = encoded_labels

# 편평화(flatten)를 위한 함수 정의
def flatten_data(dataset):
    flattened_data = []
    for i in range(len(dataset['question'])):
        flattened_data.append({
            'question': dataset['question'][i],
            'label_ids': dataset['label_ids'][i],
            'image': dataset['image'][i],
        })
    return flattened_data

# 편평화 진행
flattened_data = flatten_data(used_data)

# 결과 출력
for data_point in flattened_data:
    print("편평화된 데이터 포인트:")
    print(f"질문: {data_point['question']}")
    print(f"라벨 ID: {data_point['label_ids']}")
    print(f"이미지: {data_point['image']}")
    print()

# 첫 번째 편평화된 데이터 포인트 출력
print(flattened_data[0])








Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/pip/_vendor/pkg_resources/__init__.py", line 3109, in _dep_map
    return self.__dep_map
  File "/usr/local/lib/python3.10/dist-packages/pip/_vendor/pkg_resources/__init__.py", line 2902, in __getattr__
    raise AttributeError(attr)
AttributeError: _DistInfoDistribution__dep_map

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/pip/_internal/cli/base_command.py", line 180, in exc_logging_wrapper
    status = run_func(*args)
  File "/usr/local/lib/python3.10/dist-packages/pip/_internal/cli/req_command.py", line 245, in wrapper
    return func(self, options, args)
  File "/usr/local/lib/python3.10/dist-packages/pip/_internal/commands/install.py", line 444, in run
    conflicts = self._determine_conflicts(to_install)
  File "/usr/local/lib/python3.10/dist-packages/pip/_internal/commands/install.py", line 

Type of used_data: <class 'dict'>
New Data Point:
question: ['What is the hairstyle of the blond called?', 'How old do you have to be in canada to do this?', 'Can you guess the place where the man is playing?', 'Which rail company is named after a town in new mexico?', 'Is the boy swimming or doing another water activity?', 'Why do kids stare?', 'When was this piece of sporting equipment invented?', 'Why is this officer using this mode of transportation?', 'Why is this an atypical look for someone wearing this makeup?', 'Which american president is most associated with the stuffed animal seen here?', 'Which breed of dog it this?', 'What is the name of the famous dreamworks animated film where this animal was voiced by chris rock?', 'What objects is this person using to help them ski?', 'Has this guy shaved his beard today how do you know?', 'Where would i find this room?', 'What toy store used a mascot similar to these animals for many years?', 'What would the red bottle next to the si

In [108]:
!pip install -q transformers pytorch-lightning
!pip install pandas
! pip install transformers datasets evaluate
! pip install timm
! pip install -U accelerate

In [36]:
#(1) hugging face에 write token으로 로그인
#로그인을 해야 train 가능
from huggingface_hub import notebook_login

notebook_login()

In [37]:
import pandas as pd
from datasets import load_dataset
import numpy as np
import os
from PIL import Image, ImageDraw
import random
from transformers import AutoImageProcessor, AutoModel, TrainingArguments, Trainer, pipeline
import albumentations
import numpy as np
import torch
import json
import torchvision
import evaluate
from tqdm import tqdm
import requests
from sklearn.preprocessing import LabelEncoder




In [38]:
use_data = load_dataset("Multimodal-Fatima/OK-VQA_train")


In [39]:
# 처음 200개의 데이터를 가져옵니다.
used_data = use_data['train'][:200]

# 데이터셋의 구조 확인
print(f"Type of used_data: {type(used_data)}")

# 선택할 특성
selected_features_to_keep = ['question', 'answers', 'image']

# 새로운 데이터를 담을 리스트 초기화
new_data = []

# 기존 데이터에서 선택한 특성만 포함한 새로운 데이터 생성
new_data_point = {feature: used_data.get(feature) for feature in selected_features_to_keep}
new_data.append(new_data_point)

# 결과 출력
for data_point in new_data:
    print("New Data Point:")
    for feature in selected_features_to_keep:
        print(f"{feature}: {data_point.get(feature)}")
    print()


Type of used_data: <class 'dict'>
New Data Point:
question: ['What is the hairstyle of the blond called?', 'How old do you have to be in canada to do this?', 'Can you guess the place where the man is playing?', 'Which rail company is named after a town in new mexico?', 'Is the boy swimming or doing another water activity?', 'Why do kids stare?', 'When was this piece of sporting equipment invented?', 'Why is this officer using this mode of transportation?', 'Why is this an atypical look for someone wearing this makeup?', 'Which american president is most associated with the stuffed animal seen here?', 'Which breed of dog it this?', 'What is the name of the famous dreamworks animated film where this animal was voiced by chris rock?', 'What objects is this person using to help them ski?', 'Has this guy shaved his beard today how do you know?', 'Where would i find this room?', 'What toy store used a mascot similar to these animals for many years?', 'What would the red bottle next to the si

In [40]:

# 'answers'의 첫 번째 답변만 선택
selected_answers = [ans[0] for ans in used_data['answers']]

# LabelEncoder를 사용하여 답변을 id로 매핑
label_encoder = LabelEncoder()
encoded_labels = label_encoder.fit_transform(selected_answers)

# 매핑된 id를 데이터셋에 추가
used_data['label_ids'] = encoded_labels

# 편평화(flatten)를 위한 함수 정의
def flatten_data(dataset):
    flattened_data = []
    for i in range(len(dataset['question'])):
        flattened_data.append({
            'question': dataset['question'][i],
            'label_ids': dataset['label_ids'][i],
            'image': dataset['image'][i],
        })
    return flattened_data

# 편평화 진행
flattened_data = flatten_data(used_data)

# 결과 출력
for data_point in flattened_data:
    print("편평화된 데이터 포인트:")
    print(f"질문: {data_point['question']}")
    print(f"라벨 ID: {data_point['label_ids']}")
    print(f"이미지: {data_point['image']}")
    print()



편평화된 데이터 포인트:
질문: What is the hairstyle of the blond called?
라벨 ID: 138
이미지: <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=640x479 at 0x7B39B9F36A10>

편평화된 데이터 포인트:
질문: How old do you have to be in canada to do this?
라벨 ID: 7
이미지: <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=640x428 at 0x7B39B9F37610>

편평화된 데이터 포인트:
질문: Can you guess the place where the man is playing?
라벨 ID: 26
이미지: <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=500x333 at 0x7B39B9F37790>

편평화된 데이터 포인트:
질문: Which rail company is named after a town in new mexico?
라벨 ID: 155
이미지: <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=640x301 at 0x7B39B9F36530>

편평화된 데이터 포인트:
질문: Is the boy swimming or doing another water activity?
라벨 ID: 22
이미지: <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=640x458 at 0x7B39B9F37520>

편평화된 데이터 포인트:
질문: Why do kids stare?
라벨 ID: 55
이미지: <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=640x491 at 0x7B39B9F36620>

편평화된 데이터 포인트:
질문: When was this pi

In [75]:
# 첫 번째 편평화된 데이터 포인트 출력
print(flattened_data[0])


{'question': 'What is the hairstyle of the blond called?', 'label_ids': 138, 'image': <PIL.JpegImagePlugin.JpegImageFile image mode=RGB size=640x479 at 0x7B39B8FF5F60>}


In [110]:
import torch
from transformers import AutoTokenizer, AutoModel
from torch.utils.data import DataLoader, TensorDataset
from transformers import AdamW
from transformers import Trainer
# (1) Fine-tuning할 모델 가져오기
model_name = "microsoft/git-base-vqav2"
model = AutoModel.from_pretrained(model_name)




# (2) BertTokenizerFast로 텍스트 토크나이즈
tokenizer = AutoTokenizer.from_pretrained(model_name)

# 예제 문장
text = "생명, 우주, 그리고 모든 것에 대한 궁극적인 질문의 답은 무엇인가요?"
label = 42

# 텍스트를 토크나이즈하고 입력 형식에 맞게 변환
inputs = tokenizer(text, return_tensors="pt")
input_ids = inputs["input_ids"]
attention_mask = inputs["attention_mask"]

# (3) 배치 생성 및 모델 초기화
# 예제 데이터
texts = ["인생의 의미는 무엇인가요?", "프랑스의 수도는 어디인가요?", "로미오와 줄리엣을 쓴 작가는 누구인가요?", "2 더하기 2는 무엇인가요?"]
labels = torch.tensor([42, 0, 1, 4])

# 텍스트를 토크나이즈하고 입력 형식에 맞게 변환
tokenized = tokenizer(texts, return_tensors="pt", padding=True, truncation=True)

# 입력 데이터셋 생성
dataset = TensorDataset(tokenized["input_ids"], tokenized["attention_mask"], labels)

# DataLoader 생성
batch_size = 8
dataloader = DataLoader(dataset, batch_size=batch_size, shuffle=True)

# AdamW 옵티마이저 설정
optimizer = AdamW(model.parameters(), lr=5e-5)

# (4) Fine-tuning하기
epochs = 20

for epoch in range(epochs):
    total_loss = 0
    model.train()

    for batch in dataloader:
        input_ids, attention_mask, labels = batch

        optimizer.zero_grad()

        outputs = model(input_ids=input_ids, attention_mask=attention_mask)
        logits = outputs.last_hidden_state

        # 손실을 계산하고 역전파
        logits_flat = logits.view(-1, logits.size(-1))  # 평탄화
        labels_flat = labels.view(-1)

        # 레이블과 예측의 크기가 일치하도록 배치 크기를 조절
        logits_flat = logits_flat[:labels_flat.size(0), :]

        loss = torch.nn.functional.cross_entropy(logits_flat, labels_flat)
        total_loss += loss.item()

        loss.backward()
        optimizer.step()

    average_loss = total_loss / len(dataloader)
    print(f"Epoch {epoch + 1}/{epochs}, Loss: {average_loss}")

# Fine-tuning이 완료된 모델을 저장하려면 아래 코드를 추가합니다.
model.save_pretrained("chojo12/task4")
tokenizer.save_pretrained("chojo12/task4")




/usr/local/lib/python3.10/dist-packages/transformers/optimization.py:411: FutureWarning: This implementation of AdamW is deprecated and will be removed in a future version. Use the PyTorch implementation torch.optim.AdamW instead, or set `no_deprecation_warning=True` to disable this warning
  warnings.warn(


Epoch 1/20, Loss: 7.648337364196777
Epoch 2/20, Loss: 4.4959611892700195
Epoch 3/20, Loss: 5.166015625
Epoch 4/20, Loss: 4.7986297607421875
Epoch 5/20, Loss: 2.5234715938568115
Epoch 6/20, Loss: 2.0825278759002686
Epoch 7/20, Loss: 3.4401731491088867
Epoch 8/20, Loss: 3.169785976409912
Epoch 9/20, Loss: 3.463315725326538
Epoch 10/20, Loss: 3.2633056640625
Epoch 11/20, Loss: 3.630765676498413
Epoch 12/20, Loss: 2.84836483001709
Epoch 13/20, Loss: 2.2839784622192383
Epoch 14/20, Loss: 1.7288882732391357
Epoch 15/20, Loss: 1.3944531679153442
Epoch 16/20, Loss: 1.4189079999923706
Epoch 17/20, Loss: 1.8800429105758667
Epoch 18/20, Loss: 2.3808255195617676
Epoch 19/20, Loss: 3.0462162494659424
Epoch 20/20, Loss: 2.2001445293426514


('chojo12/task4/tokenizer_config.json',
 'chojo12/task4/special_tokens_map.json',
 'chojo12/task4/vocab.txt',
 'chojo12/task4/added_tokens.json',
 'chojo12/task4/tokenizer.json')